In [17]:
import urllib.request
import pandas as pd
import seaborn as sns
import numpy as np
import matplotlib.pyplot as plt
import geopandas as gpd
import altair as alt
from urllib.request import Request, urlopen
import requests
import json
from shapely.geometry import MultiPoint
from pandas.io.json import json_normalize
import os


## Load healthcare data

In [18]:
with open('Census_2010_Tracts_NoHealthInsurance.json') as f:
    data = json.load(f)  
    data["features"]


vertical_stack=pd.DataFrame()

for d in data["features"]:
    df=json_normalize(d)
    vertical_stack = pd.concat([vertical_stack, df], axis=0)

#vertical_stack.drop_duplicates(keep=False)

In [19]:
vertical_stack.head(3)

#key variable: attributes.health_acs19nohi

attributes.OBJECTID  attributes.FID  attributes.OBJECTID_1  \
0                    1               1                      1   
0                    2               2                      2   
0                    3               3                      3   

  attributes.STATEFP10 attributes.COUNTYFP10 attributes.TRACTCE10  \
0                   25                   025               010405   
0                   25                   025               010404   
0                   25                   025               010801   

  attributes.GEOID10 attributes.NAME10 attributes.NAMELSAD10  \
0        25025010405            104.05   Census Tract 104.05   
0        25025010404            104.04   Census Tract 104.04   
0        25025010801            108.01   Census Tract 108.01   

  attributes.MTFCC10  ... attributes.Shape__Area  attributes.Shape__Length  \
0              G5020  ...          666099.906250               6036.192858   
0              G5020  ...          250612.402344               2176.592125   
0              G5020  ...          234357.902344               2542.042976   

        attributes.aggregationMethod attributes.HasData  \
0  BlockApportionment:US.BlockGroups                  1   
0  BlockApportionment:US.BlockGroups                  1   
0  BlockApportionment:US.BlockGroups                  1   

  attributes.ORIGINAL_OID  attributes.sourceCountry  \
0                       1                        US   
0                       2                        US   
0                       3                        US   

   attributes.health_acs19nohi  attributes.Shape_Length  \
0                           59                 0.046607   
0                          253                 0.017437   
0                           21                 0.021368   

   attributes.Shape_Area                                     geometry.rings  
0               0.000040  [[[-71.09008759999995, 42.34666567000005], [-7...  
0               0.000015  [[[-71.09066059999998, 42.339774669000064], [-...  
0               0.000014  [[[-71.08159559799998, 42.35371267100004], [-7...  

[3 rows x 27 columns]

In [20]:
vertical_stack["attributes.NAME10"].unique()

array(['104.05', '104.04', '108.01', '107.02', '102.04', '108.02',
       '101.04', '7.03', '5.04', '7.04', '101.03', '8.03', '9803',
       '1202.01', '1201.04', '1106.07', '3.02', '3.01', '1404', '1403',
       '1402.01', '1402.02', '1401.02', '1304.02', '1303', '1302', '1301',
       '1207', '1206', '1205', '1204', '1106.01', '1105.02', '1105.01',
       '1104.01', '1011.02', '1011.01', '1010.02', '1010.01', '1009',
       '1008', '1006.01', '1005', '1004', '1003', '9813', '9812.01',
       '9815.01', '9817', '9818', '1002', '1001', '924', '923', '922',
       '920', '919', '918', '917', '916', '9811', '1401.05', '9807',
       '1201.05', '1203.01', '712.01', '910.01', '915', '914', '913',
       '912', '911', '907', '906', '904', '903', '902', '9801.01',
       '408.01', '102.03', '1104.03', '1102.01', '9810', '901', '821',
       '820', '819', '818', '817', '815', '814', '813', '1101.03',
       '1103.01', '1401.06', '107.01', '104.08', '5.03', '812', '811',
       '809', '808.01'

In [21]:
vertical_stack.rename(columns = {'attributes.health_acs19nohi':'nohi'}, inplace = True)
vertical_stack.rename(columns = {'attributes.NAME10':'NAME10'}, inplace = True)

## Open census tract 2010 shape file

In [22]:
#open json file
shape_file_loc = './Census_2010_Tracts/Census_2010_Tracts.shp'

gdf=gpd.read_file(shape_file_loc)

gdf.head(2)

FID  OBJECTID STATEFP10 COUNTYFP10 TRACTCE10      GEOID10  NAME10  \
0    1         1        25        025    010405  25025010405  104.05   
1    2         2        25        025    010404  25025010404  104.04   

            NAMELSAD10 MTFCC10 FUNCSTAT10  ALAND10  AWATER10   INTPTLAT10  \
0  Census Tract 104.05   G5020          S   363702         0  +42.3398654   
1  Census Tract 104.04   G5020          S   136829         0  +42.3419667   

     INTPTLON10    Shape_STAr    Shape_STLe     Shape__Are   Shape__Len  \
0  -071.0896052  3.914568e+06  14629.550361  666099.906250  6036.192858   
1  -071.0886375  1.472714e+06   5277.643216  250612.402344  2176.592125   

                                            geometry  
0  POLYGON ((-71.09009 42.34667, -71.09001 42.346...  
1  POLYGON ((-71.09066 42.33977, -71.09103 42.339...

## Merge two datasets together

In [23]:
hc_final= pd.merge(gdf,vertical_stack, how='left', on=['NAME10'])

In [24]:
hc_final.head(3)

FID  OBJECTID STATEFP10 COUNTYFP10 TRACTCE10      GEOID10  NAME10  \
0    1         1        25        025    010405  25025010405  104.05   
1    2         2        25        025    010404  25025010404  104.04   
2    3         3        25        025    010801  25025010801  108.01   

            NAMELSAD10 MTFCC10 FUNCSTAT10  ...  attributes.Shape__Area  \
0  Census Tract 104.05   G5020          S  ...           666099.906250   
1  Census Tract 104.04   G5020          S  ...           250612.402344   
2  Census Tract 108.01   G5020          S  ...           234357.902344   

   attributes.Shape__Length       attributes.aggregationMethod  \
0               6036.192858  BlockApportionment:US.BlockGroups   
1               2176.592125  BlockApportionment:US.BlockGroups   
2               2542.042976  BlockApportionment:US.BlockGroups   

  attributes.HasData  attributes.ORIGINAL_OID  attributes.sourceCountry  \
0                1.0                      1.0                        US   
1                1.0                      2.0                        US   
2                1.0                      3.0                        US   

    nohi  attributes.Shape_Length attributes.Shape_Area  \
0   59.0                 0.046607              0.000040   
1  253.0                 0.017437              0.000015   
2   21.0                 0.021368              0.000014   

                                      geometry.rings  
0  [[[-71.09008759999995, 42.34666567000005], [-7...  
1  [[[-71.09066059999998, 42.339774669000064], [-...  
2  [[[-71.08159559799998, 42.35371267100004], [-7...  

[3 rows x 45 columns]

## Extract the center points

In [25]:
hc_final['centroid_lon'] = gdf['geometry'].centroid.x
hc_final['centroid_lat'] = gdf['geometry'].centroid.y

## Examine null data and drop null

In [26]:
hc_final.isna().sum()

null_data = hc_final[hc_final.isnull().any(axis=1)]

In [27]:
hc_final=hc_final.dropna()



## Merge that dataset now with median household income 2019

In [28]:
with open('Census_2010_Tracts_MedianHouseHold.json') as f:
    data = json.load(f)  



vertical_stack=pd.DataFrame()

for d in data["features"]:
    df=json_normalize(d)
    vertical_stack = pd.concat([vertical_stack, df], axis=0)

    
vertical_stack["attributes.NAME10"].unique()

vertical_stack.rename(columns = {'attributes.NAME10':'NAME10'}, inplace = True)

vertical_stack.head(2)

final= pd.merge(hc_final,vertical_stack, how='left', on=['NAME10'])



In [29]:
final.rename(columns = {'attributes.householdincome_medhinc_cy':'median_hhic'}, inplace = True)

In [30]:
final.head(3)

FID  OBJECTID STATEFP10 COUNTYFP10 TRACTCE10      GEOID10  NAME10  \
0    1         1        25        025    010405  25025010405  104.05   
1    2         2        25        025    010404  25025010404  104.04   
2    3         3        25        025    010801  25025010801  108.01   

            NAMELSAD10 MTFCC10 FUNCSTAT10  ...  attributes.Shape__Area_y  \
0  Census Tract 104.05   G5020          S  ...             666099.906250   
1  Census Tract 104.04   G5020          S  ...             250612.402344   
2  Census Tract 108.01   G5020          S  ...             234357.902344   

   attributes.Shape__Length_y     attributes.aggregationMethod_y  \
0                 6036.192858  BlockApportionment:US.BlockGroups   
1                 2176.592125  BlockApportionment:US.BlockGroups   
2                 2542.042976  BlockApportionment:US.BlockGroups   

  attributes.HasData_y  attributes.ORIGINAL_OID_y  attributes.sourceCountry_y  \
0                    1                          1                          US   
1                    1                          2                          US   
2                    1                          3                          US   

   median_hhic  attributes.Shape_Length_y attributes.Shape_Area_y  \
0        18632                   0.046607                0.000040   
1        19638                   0.017437                0.000015   
2       153010                   0.021368                0.000014   

                                    geometry.rings_y  
0  [[[-71.09008759999995, 42.34666567000005], [-7...  
1  [[[-71.09066059999998, 42.339774669000064], [-...  
2  [[[-71.08159559799998, 42.35371267100004], [-7...  

[3 rows x 73 columns]

In [31]:
final.isna().sum() #one null

null_data = final[final.isnull().any(axis=1)]

null_data

Empty GeoDataFrame
Columns: [FID, OBJECTID, STATEFP10, COUNTYFP10, TRACTCE10, GEOID10, NAME10, NAMELSAD10, MTFCC10, FUNCSTAT10, ALAND10, AWATER10, INTPTLAT10, INTPTLON10, Shape_STAr, Shape_STLe, Shape__Are, Shape__Len, geometry, attributes.OBJECTID_x, attributes.FID_x, attributes.OBJECTID_1_x, attributes.STATEFP10_x, attributes.COUNTYFP10_x, attributes.TRACTCE10_x, attributes.GEOID10_x, attributes.NAMELSAD10_x, attributes.MTFCC10_x, attributes.FUNCSTAT10_x, attributes.ALAND10_x, attributes.AWATER10_x, attributes.INTPTLAT10_x, attributes.INTPTLON10_x, attributes.Shape_STAr_x, attributes.Shape_STLe_x, attributes.Shape__Area_x, attributes.Shape__Length_x, attributes.aggregationMethod_x, attributes.HasData_x, attributes.ORIGINAL_OID_x, attributes.sourceCountry_x, nohi, attributes.Shape_Length_x, attributes.Shape_Area_x, geometry.rings_x, centroid_lon, centroid_lat, attributes.OBJECTID_y, attributes.FID_y, attributes.OBJECTID_1_y, attributes.STATEFP10_y, attributes.COUNTYFP10_y, attributes.TRACTCE10_y, attributes.GEOID10_y, attributes.NAMELSAD10_y, attributes.MTFCC10_y, attributes.FUNCSTAT10_y, attributes.ALAND10_y, attributes.AWATER10_y, attributes.INTPTLAT10_y, attributes.INTPTLON10_y, attributes.Shape_STAr_y, attributes.Shape_STLe_y, attributes.Shape__Area_y, attributes.Shape__Length_y, attributes.aggregationMethod_y, attributes.HasData_y, attributes.ORIGINAL_OID_y, attributes.sourceCountry_y, median_hhic, attributes.Shape_Length_y, attributes.Shape_Area_y, geometry.rings_y]
Index: []

[0 rows x 73 columns]

In [32]:
json = json.loads(final.to_json())
data = alt.Data(values=json['features'])


In [83]:
selection= alt.selection_single(empty='none', on="mouseover")

base = alt.Chart(data).mark_geoshape(
    stroke="black",
    strokeWidth=3,
    ).encode(
    color=alt.Color("properties.nohi:Q",legend=alt.Legend(title="Uninsured population"),
                    bin=True,
                    scale=alt.Scale(scheme="purplebluegreen")
  ),
    strokeWidth=alt.condition(selection, alt.value(3), alt.value(0)),
    opacity=alt.condition(selection, alt.value(1), alt.value(0.8)),
    tooltip=[alt.Tooltip("properties.NAME10:N",title="Census Tract"),alt.Tooltip("properties.nohi:Q", title="Uninsured population")]
).properties(
        width=350,
        height=300
    ).add_selection(selection).properties(height=300, width=350)


In [84]:
base

alt.Chart(...)

In [87]:
colorCondition = alt.condition(selection,alt.value("red"),
                      alt.Color("properties.median_hhic:Q",legend=None, bin=True,
                                scale=alt.Scale(scheme="oranges")))

points= alt.Chart(data).mark_point(filled=True, size=80).encode(
    x=alt.X("properties.median_hhic:Q",sort="-y", title="Meidan Household Income 2019"),
    y=alt.Y('properties.nohi:Q', axis=alt.Axis(orient='right'), title="Uninsured Population"),
    tooltip=[alt.Tooltip('properties.median_hhic:Q', title="Median HH Income"),alt.Tooltip("properties.NAMELSAD10:N", title="Census Tract")],
    color=colorCondition
    ).properties(height=300, width=350)


In [88]:
no_ins=(base|points).resolve_legend(
     color="independent",
).add_selection(selection)

no_ins

alt.HConcatChart(...)

In [89]:
no_ins.save('no_insurance_income.json')

In [21]:
no_ins.save('no_insurance_income.html')

## Create base map and add labels

In [21]:
selection=alt.selection_single(empty='none', on="mouseover")

#open json file
###CREATE BASE LAYER
from pandas.io.json import json_normalize

# Download Geojson
def download_json():
    '''Downloads GEOJSON'''
    url = "https://opendata.arcgis.com/datasets/3525b0ee6e6b427f9aab5d0a1d0a1a28_0.geojson"
    resp = requests.get(url)
    data=resp.json()
    
    with open('GeoBoston.json', 'w') as f:
        json.dump(data, f)
        
    return data

download_json()

with open('GeoBoston.json') as f:
    boston_json=json.load(f)

#extract only "features"
boston_data = alt.Data(values=boston_json['features'])

boston_data


##create base map
base_neighborhood = alt.Chart(boston_data).mark_geoshape(
    stroke='gray',
    fill=None,
    strokeWidth=2
    ).encode(
    #color=alt.Color("properties.Name:N",scale=alt.Scale(scheme='category20')),
    tooltip=["properties.Name:N","properties.Acres:Q"]
    )

base_neighborhood


AttributeError: 'dict' object has no attribute 'dump'

In [ ]:
#create selection 
list_boston=boston_json['features']
all_names=[]


for i in list_boston: 
    all_names.append(i["properties"]["Name"])
    
input_dropdown = alt.binding_select(options=all_names)


selection = alt.selection_single(fields=['properties.Name'], bind=input_dropdown, name=' Neighborhoods', empty="none")

##create base map
base_neighborhood = alt.Chart(boston_data).mark_geoshape(
    stroke="darkblue",
    fill=None,
    ).encode(
    strokeWidth=alt.condition(selection, alt.value(3), alt.value(0)),
    ).add_selection(selection)

base_neighborhood

In [ ]:
#create label

###ADD NEIGHBORHOOD ID
geojson = download_json()

#convert geojson to pandas data frame 
gdf = gpd.GeoDataFrame.from_features((geojson))

#create new columns: lontitude and latitude
gdf['lon'] = gdf['geometry'].centroid.x
gdf['lat'] = gdf['geometry'].centroid.y

gdf.head(2)

In [ ]:
labels = alt.Chart(gdf).mark_text(
    baseline='middle', 
    fontWeight=900,
    fontSize=10, 
    align="center",
    opacity=0.7,
    color="#e6959c"
    #fontStyle="italic"
).encode(
    longitude='lon',
    latitude='lat',
    text=('Name'),
     ).properties(
        width=350,
        height=300
    ).transform_filter(
    alt.FieldOneOfPredicate(field='Neighborhood_ID', oneOf=["25","24","19","10","15","12","11","16","6","17","29","4","8","22"])
)


In [ ]:
final=alt.concat(
    base_neighborhood+base+labels,
).configure_title(fontSize=12)

final.save("HealthInsurance.json")

In [ ]:
final